Задание:

Вас пригласили работать в картографический сервис, в котором давно собирают пользовательский контент, но технически не реализовали сбор рейтинга у отзыва. Вам нужно по существующим отзывам Яндекс Карт обучиться и определить рейтинг (от 1 до 5) произвольного отзыва.

Данные:
обучение: https://github.com/yandex/geo-reviews-dataset-2023
предсказание — прилагаю следующим сообщением

Ограничения:
запрещается использовать внешние LLM-ки (которые не запускаются у вас локально = ChatGPT, Gemini и др.) для оценивания примеров, аугментации датасета и т.п.
Пробовать писать код с помощью неё можете :)

Метрика:
RMSE на тестовом датасете
Паблик тест — 16%
Прайват тест — 84%

Формат файла для отправки:
tsv (tab separated values). заголовок отсутсвует
первый столбец — id отзыва (int)
второй столбец — предсказанный рейтинг отзыва (float)

Определение итогов:
последнее присланное решение будет оцениваться на прайват тесте. По результатам прайват теста сформируем итоговые результаты


# Готовим библиотеки и скачиваем данные для обучения



In [ ]:
!wget -O reviews.tskv https://github.com/yandex/geo-reviews-dataset-2023/raw/refs/heads/master/geo-reviews-dataset-2023.tskv?download=

--2024-12-15 16:55:26--  https://github.com/yandex/geo-reviews-dataset-2023/raw/refs/heads/master/geo-reviews-dataset-2023.tskv?download=
Resolving github.com (github.com)... 140.82.112.4
Connecting to github.com (github.com)|140.82.112.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://media.githubusercontent.com/media/yandex/geo-reviews-dataset-2023/refs/heads/master/geo-reviews-dataset-2023.tskv?download=true [following]
--2024-12-15 16:55:26--  https://media.githubusercontent.com/media/yandex/geo-reviews-dataset-2023/refs/heads/master/geo-reviews-dataset-2023.tskv?download=true
Resolving media.githubusercontent.com (media.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to media.githubusercontent.com (media.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 378730064 (361M) [application/octet-stream]
Saving to: ‘reviews.tskv’

reviews.tskv  

In [ ]:
!pip install fasttext

# Сохраняем данные в pandas dataframe

In [ ]:
data = []
with open("reviews.tskv") as f:
    for line in f:
        item_to_save = {}
        for key_val in line.split("\t"):
            key, val = key_val.split("=", 1)
            item_to_save[key] = val
        data.append(item_to_save)


In [ ]:
import pandas as pd

In [ ]:
data[0]

{'address': 'Екатеринбург, ул. Московская / ул. Волгоградская / ул. Печатников',
 'name_ru': 'Московский квартал',
 'rating': '3.',
 'rubrics': 'Жилой комплекс',
 'text': 'Московский квартал 2.\\nШумно : летом по ночам дикие гонки. Грязно : кругом стройки, невозможно открыть окна (16 этаж! ), вечно по району летает мусор. Детские площадки убогие, на большой площади однотипные конструкции. Очень дорогая коммуналка. Часто срабатывает пожарная сигнализация. Жильцы уже не реагируют. В это время, обычно около часа, не работают лифты. Из плюсов - отличная планировка квартир ( Московская 194 ), на мой взгляд. Ремонт от застройщика на 3-. Окна вообще жуть - вместо вентиляции. По соотношению цена/качество - 3.\n'}

In [ ]:
data = pd.DataFrame.from_dict(data)
data["rating"] = data["rating"].astype(float)

In [ ]:
data.head()

address             name_ru  \
0  Екатеринбург, ул. Московская / ул. Волгоградск...  Московский квартал   
1  Московская область, Электросталь, проспект Лен...   Продукты Ермолино   
2  Краснодар, Прикубанский внутригородской округ,...             LimeFit   
3   Санкт-Петербург, проспект Энгельса, 111, корп. 1        Snow-Express   
4                  Тверь, Волоколамский проспект, 39  Студия Beauty Brow   

   rating                                            rubrics  \
0     3.0                                     Жилой комплекс   
1     5.0  Магазин продуктов;Продукты глубокой заморозки;...   
2     1.0                                        Фитнес-клуб   
3     4.0        Пункт проката;Прокат велосипедов;Сапсёрфинг   
4     5.0  Салон красоты;Визажисты, стилисты;Салон бровей...   

                                                text  
0  Московский квартал 2.\nШумно : летом по ночам ...  
1  Замечательная сеть магазинов в общем, хороший ...  
2  Не знаю смутят ли кого-то данные правила, но я...  
3  Хорошие условия аренды. \nДружелюбный персонал...  
4  Топ мастер Ангелина топ во всех смыслах ) Немн...

In [ ]:
data["rating"].value_counts()

rating
5.0    390515
4.0     41160
1.0     34351
3.0     21686
2.0     12088
0.0       200
Name: count, dtype: int64

In [ ]:
# предварительно тестовые данные тоже сохраним в dataframe. они не tskv, а tsv, поэтому пользуемся pd.read_csv
data_test_to_eval = pd.read_csv("data_test_to_evaluate.tsv", sep="\t")


# бейзлайн решение. const = 3

In [ ]:
data_test_to_eval.head()

Unnamed: 0                                        review_text
0           0  Туда сложно попасть. Многие спрашивают не знае...
1           1  Почта России с недавних пор стала продвинутой ...
2           2  Живу рядом, в соседнем доме. Стены дрожат в бу...
3           3  Всем привет, никогда в жизни не писал никакие ...
4           4  Бизнес ланч не понравился, не смотря на большо...

In [ ]:
data_test_to_eval["rating"] = 3.

In [ ]:
data_test_to_eval.head()

Unnamed: 0                                        review_text  rating
0           0  Туда сложно попасть. Многие спрашивают не знае...     3.0
1           1  Почта России с недавних пор стала продвинутой ...     3.0
2           2  Живу рядом, в соседнем доме. Стены дрожат в бу...     3.0
3           3  Всем привет, никогда в жизни не писал никакие ...     3.0
4           4  Бизнес ланч не понравился, не смотря на большо...     3.0

In [ ]:
data_test_to_eval[["Unnamed: 0", "rating"]].to_csv("submit_3_const.tsv", sep="\t", header=None, index=None)

# 2. Обучим фасттекст

In [ ]:
data = data.loc[data["rating"]!=0., :]

In [ ]:
data.head()

address             name_ru  \
0  Екатеринбург, ул. Московская / ул. Волгоградск...  Московский квартал   
1  Московская область, Электросталь, проспект Лен...   Продукты Ермолино   
2  Краснодар, Прикубанский внутригородской округ,...             LimeFit   
3   Санкт-Петербург, проспект Энгельса, 111, корп. 1        Snow-Express   
4                  Тверь, Волоколамский проспект, 39  Студия Beauty Brow   

   rating                                            rubrics  \
0     3.0                                     Жилой комплекс   
1     5.0  Магазин продуктов;Продукты глубокой заморозки;...   
2     1.0                                        Фитнес-клуб   
3     4.0        Пункт проката;Прокат велосипедов;Сапсёрфинг   
4     5.0  Салон красоты;Визажисты, стилисты;Салон бровей...   

                                                text  
0  Московский квартал 2.\nШумно : летом по ночам ...  
1  Замечательная сеть магазинов в общем, хороший ...  
2  Не знаю смутят ли кого-то данные правила, но я...  
3  Хорошие условия аренды. \nДружелюбный персонал...  
4  Топ мастер Ангелина топ во всех смыслах ) Немн...

In [ ]:
# грязно сбалансируем датасет, удалив огромное количество 5* отзывов
RATING_COUNT_MAX = 50000
data_small = pd.DataFrame(data.loc[data["rating"] < 5, :])
data_small = pd.concat([data_small,data.loc[data["rating"] == 5, :].iloc[:RATING_COUNT_MAX,:]], ignore_index=True)

# сбалансируем, оставив только столько отзывов 1,2,3,4,5, сколько минимально отзывов, соответствующих одному числу (рейтингу 2 всего 12088 значений)
# df_2_min = data[data['rating'] == 2]
# print('df_2_min.shape = ', df_2_min.shape)
# df1 = data[data['rating'] == 1].sample(df_2_min.shape[0])
# df3 = data[data['rating'] == 3].sample(df_2_min.shape[0])
# df4 = data[data['rating'] == 4].sample(df_2_min.shape[0])
# df5 = data[data['rating'] == 5].sample(df_2_min.shape[0])
# data_small = pd.concat([df1, df_2_min, df3, df4, df5], ignore_index=True)
# data_small

In [ ]:
import fasttext
import fasttext.util
import numpy as np

# Download the pre-trained model for a specific language if necessary
# fasttext.util.download_model('en', if_necessary=True)  # English

# Load a pre-trained model (change 'cc.en.300.bin' to your downloaded model file)
#fasttext.util.download_model('ru', if_exists='ignore')


In [ ]:
#предобученные ру эмбэды
!wget -O cc.ru.300.bin.gz https://dl.fbaipublicfiles.com/fasttext/vectors-crawl/cc.ru.300.bin.gz

--2024-11-29 19:31:38--  https://dl.fbaipublicfiles.com/fasttext/vectors-crawl/cc.ru.300.bin.gz
Resolving dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)... 13.226.210.25, 13.226.210.111, 13.226.210.78, ...
Connecting to dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)|13.226.210.25|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4496459151 (4.2G) [application/octet-stream]
Saving to: ‘cc.ru.300.bin.gz’

cc.ru.300.bin.gz    100%[===================>]   4.19G  84.2MB/s    in 48s     

2024-11-29 19:32:25 (90.2 MB/s) - ‘cc.ru.300.bin.gz’ saved [4496459151/4496459151]



In [ ]:
!gzip -d cc.ru.300.bin.gz

In [ ]:
model = fasttext.load_model('cc.ru.300.bin')  # make sure the file path is correct

In [ ]:
# def compute_word_embedding(word):
#     return model.get_word_vector(word)

# def compute_sentence_embedding(sentence):
#     sentence = sentence.replace(",", "").replace("!", "").replace(".", "").replace("?", "")
#     sentence = sentence.replace("\n", " ")
#     sentence = sentence.lower()
#     words = sentence.split()
#     word_embeddings = [compute_word_embedding(word) for word in words]
#     word_embeddings_mean = np.mean(word_embeddings, axis=0)
#     #sentence_embedding = word_embeddings_mean
#     sentence_embedding = word_embeddings_mean / max(0.0001, np.linalg.norm(word_embeddings_mean))

#     return sentence_embedding

import fasttext
from tqdm.notebook import tqdm
import re

!wget -O cc.ru.300.bin.gz https://dl.fbaipublicfiles.com/fasttext/vectors-crawl/cc.ru.300.bin.gz

!gzip -d cc.ru.300.bin.gz

model = fasttext.load_model('cc.ru.300.bin')  # Убедитесь, что путь к файлу верный

def compute_word_embedding(word):
    return model.get_word_vector(word)

def compute_sentence_embedding(sentence):
    # Очистка и предварительная обработка предложения
    sentence = re.sub(r'[^\w\s]', '', sentence.lower())
    sentence = sentence.replace("\n", " ")
    words = sentence.split()

    if not words:
        # Возвращаем нулевой вектор, если нет слов
        return np.zeros(model.get_dimension())

    word_embeddings = [compute_word_embedding(word) for word in words]
    word_embeddings_mean = np.mean(word_embeddings, axis=0)
    norm = np.linalg.norm(word_embeddings_mean)

    if norm < 1e-4:
        # Избегаем деления на ноль или очень малые числа
        sentence_embedding = word_embeddings_mean
    else:
        sentence_embedding = word_embeddings_mean / norm

    return sentence_embedding

from sklearn.linear_model import LogisticRegression
X = []
y = []


# from transformers import AutoTokenizer, AutoModel
# import torch
# import numpy as np
# from tqdm.notebook import tqdm

# # Загрузка токенизатора и модели
# tokenizer = AutoTokenizer.from_pretrained("DeepPavlov/rubert-base-cased")
# model = AutoModel.from_pretrained("DeepPavlov/rubert-base-cased")

# def compute_sentence_embedding(sentence):
#     # Предобработка предложения
#     sentence = re.sub(r'[^\w\s]', '', sentence.lower())
#     sentence = sentence.replace("\n", " ")

#     # Токенизация
#     inputs = tokenizer(sentence, return_tensors='pt', truncation=True, padding=True)

#     # Получение эмбеддингов
#     with torch.no_grad():
#         outputs = model(**inputs)
#         hidden_states = outputs.last_hidden_state

#     # Усреднение эмбеддингов по токенам
#     sentence_embedding = torch.mean(hidden_states, dim=1).squeeze()
#     return sentence_embedding.numpy()

# # Пример использования
# X = []
# y = []

# for text, rating in tqdm(zip(data_small["text"].values, data_small["rating"].values), total=data_small.shape[0]):
#     X.append(compute_sentence_embedding(text))
    # y.append(rating)

--2024-12-15 17:42:13--  https://dl.fbaipublicfiles.com/fasttext/vectors-crawl/cc.ru.300.bin.gz
Resolving dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)... 18.238.176.126, 18.238.176.115, 18.238.176.44, ...
Connecting to dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)|18.238.176.126|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4496459151 (4.2G) [application/octet-stream]
Saving to: ‘cc.ru.300.bin.gz’

cc.ru.300.bin.gz    100%[===================>]   4.19G   214MB/s    in 21s     

2024-12-15 17:42:34 (202 MB/s) - ‘cc.ru.300.bin.gz’ saved [4496459151/4496459151]

gzip: cc.ru.300.bin already exists; do you wish to overwrite (y or n)? n
	not overwritten


In [ ]:
for text, rating in tqdm(zip(data_small["text"].values, data_small["rating"].values), total=data_small.shape[0]):
    X.append(compute_sentence_embedding(text))
    y.append(rating)

  0%|          | 0/159285 [00:00<?, ?it/s]

In [ ]:
import tqdm.notebook as tqdm

In [ ]:
# for line in tqdm.tqdm(zip(data_small["text"].values, data_small["rating"].values), total=data_small.shape[0]):
#     X.append(compute_sentence_embedding(line[0]))
#     y.append(line[1])

  0%|          | 0/159285 [00:00<?, ?it/s]

# Линейная модель на основе фасттекст эмбэдов

In [ ]:
from sklearn.linear_model import SGDRegressor

regr = SGDRegressor(max_iter=1000, tol=1e-3, eta0 = 0.1)

In [ ]:
len(X), len(y)

(159285, 159285)

In [ ]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, shuffle=True)

In [ ]:
from sklearn.metrics import root_mean_squared_error

In [ ]:
# результаты с моей балансировкой и с моими эмбедами
best_loss = float("inf")  # Инициализация для лучшего значения ошибки
best_model = None         # Переменная для хранения лучшей модели

for i in range(1000):
    # Обучение модели на текущем наборе данных
    regr.partial_fit(X_train, y_train)

    # Предсказания на тестовом наборе
    y_predict = regr.predict(X_test)

    # Вычисляем текущую метрику (RMSE)
    loss = root_mean_squared_error(y_test, y_predict)
    print(f"{i} epoch. test loss = {loss}")

    # Проверка: если текущая ошибка меньше, чем предыдущая "лучшая"
    if loss < best_loss:
        best_loss = loss
        best_model = regr  # Сохраняем текущую модель (лучшие веса)

0 epoch. test loss = 1.0607395946826834
1 epoch. test loss = 1.0390029390450424
2 epoch. test loss = 1.0285555160441031
3 epoch. test loss = 1.019680033004049
4 epoch. test loss = 1.0151251797472964
5 epoch. test loss = 1.005836240649161
6 epoch. test loss = 1.0052634422535163
7 epoch. test loss = 0.9985866451560027
8 epoch. test loss = 0.9983385915255668
9 epoch. test loss = 0.9950772123514491
10 epoch. test loss = 0.9947144751219689
11 epoch. test loss = 0.9965302374852119
12 epoch. test loss = 0.9913054559906718
13 epoch. test loss = 0.9901582523566703
14 epoch. test loss = 0.9921327107597987
15 epoch. test loss = 0.9883117359916385
16 epoch. test loss = 0.9874170864634026
17 epoch. test loss = 0.9884339062602292
18 epoch. test loss = 0.9865308036048862
19 epoch. test loss = 0.9870019611310612
20 epoch. test loss = 0.9853198680712747
21 epoch. test loss = 0.9884053429741091
22 epoch. test loss = 0.9862853638410526
23 epoch. test loss = 0.9841441662522005
24 epoch. test loss = 0.9839

In [ ]:
best_loss

0.9771142932578716

In [ ]:
for i in range(20):
    regr.partial_fit(X_train, y_train)
    y_predict = regr.predict(X_test)
    print(f"{i} epoch. test loss = ", root_mean_squared_error(y_test, y_predict))

0 epoch. test loss =  1.2123320822360506
1 epoch. test loss =  1.180921915870833
2 epoch. test loss =  1.161790232928509
3 epoch. test loss =  1.1488905440604347
4 epoch. test loss =  1.1391892496771983
5 epoch. test loss =  1.1308208628999648
6 epoch. test loss =  1.1241250769551956
7 epoch. test loss =  1.1183575765322895
8 epoch. test loss =  1.113808809154803
9 epoch. test loss =  1.1092863851005335
10 epoch. test loss =  1.1051503119793291
11 epoch. test loss =  1.1016907824522095
12 epoch. test loss =  1.0986104227561546
13 epoch. test loss =  1.0957202095340017
14 epoch. test loss =  1.093271003120616
15 epoch. test loss =  1.0908010053833799
16 epoch. test loss =  1.0884504358905427
17 epoch. test loss =  1.086364196207228
18 epoch. test loss =  1.084816112965456
19 epoch. test loss =  1.0827174353095088


In [ ]:
# делаем предсказание
X_pred = []

for line in tqdm.tqdm(data_test_to_eval["review_text"]):
    X_pred.append(compute_sentence_embedding(line))

  0%|          | 0/6211 [00:00<?, ?it/s]

In [ ]:
y_pred = regr.predict(X_pred)

In [ ]:
y_pred[:5]

array([1.45257966, 3.34878651, 2.50840725, 2.43295405, 3.76935277])

In [ ]:
pd.DataFrame(y_pred).to_csv("linreg_submit_v3.tsv", sep="\t", header=None)

# Random Forest


In [ ]:
from sklearn.ensemble import RandomForestRegressor

In [ ]:
#6000 примеров на которых нужно сделать предсказание
# leaderboard строится на основе 1000 примеров из 6000
# на основе 5к оставшихся будет строиться финальный рейтинг

In [ ]:
rf = RandomForestRegressor(n_estimators=20, max_depth=5)

In [ ]:
rf.fit(X_train, y_train)

RandomForestRegressor(max_depth=5, n_estimators=20)

In [ ]:
y_predict = rf.predict(X_test)

In [ ]:
# MSE_val на новой балансировке и новых эмбедингах
root_mean_squared_error(y_test, y_predict)

1.0986031401076302

In [ ]:
# MSE_val на старое
# root_mean_squared_error(y_test, y_predict)

1.174804545808364

In [ ]:
# сохраняем и делаем предсказание на нужном датасете
y_pred = rf.predict(X_pred)

In [ ]:
pd.DataFrame(y_pred).to_csv("rf_submit.tsv", sep="\t", header=None)

catboost

In [ ]:
!pip install catboost
!pip install ipywidgets

In [ ]:
from catboost import CatBoostRegressor

In [ ]:
cb = CatBoostRegressor(iterations=2000, learning_rate=0.1)

In [ ]:
from catboost import Pool
eval_pool = Pool(X_test, y_test)

In [ ]:
from google.colab import output
output.enable_custom_widget_manager()

In [ ]:
cb.fit(X_train, y_train, eval_set=eval_pool, use_best_model=True, plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 1.4637233	test: 1.4650234	best: 1.4650234 (0)	total: 75.7ms	remaining: 2m 31s
1:	learn: 1.4164467	test: 1.4176260	best: 1.4176260 (1)	total: 137ms	remaining: 2m 16s
2:	learn: 1.3738319	test: 1.3747361	best: 1.3747361 (2)	total: 199ms	remaining: 2m 12s
3:	learn: 1.3385346	test: 1.3389502	best: 1.3389502 (3)	total: 262ms	remaining: 2m 10s
4:	learn: 1.3073598	test: 1.3075353	best: 1.3075353 (4)	total: 322ms	remaining: 2m 8s
5:	learn: 1.2797725	test: 1.2799366	best: 1.2799366 (5)	total: 383ms	remaining: 2m 7s
6:	learn: 1.2557481	test: 1.2553993	best: 1.2553993 (6)	total: 444ms	remaining: 2m 6s
7:	learn: 1.2344948	test: 1.2338948	best: 1.2338948 (7)	total: 532ms	remaining: 2m 12s
8:	learn: 1.2157744	test: 1.2146942	best: 1.2146942 (8)	total: 593ms	remaining: 2m 11s
9:	learn: 1.1988911	test: 1.1976336	best: 1.1976336 (9)	total: 653ms	remaining: 2m 9s
10:	learn: 1.1838472	test: 1.1826545	best: 1.1826545 (10)	total: 713ms	remaining: 2m 8s
11:	learn: 1.1692689	test: 1.1678310	best: 1.

In [ ]:
y_pred = cb.predict(X_pred)

In [ ]:
y_pred[:100]

array([1.88221685, 3.96092727, 2.19828923, 1.81187261, 4.43237474,
       3.3222347 , 4.7999709 , 1.82425551, 2.03829311, 4.10178531,
       3.40819111, 5.11411769, 2.17435463, 3.92305438, 4.89424927,
       4.77029716, 1.22186444, 4.5662947 , 2.7745872 , 4.34545235,
       1.86282327, 2.56024009, 2.99806831, 4.07671448, 3.68156204,
       5.04482498, 3.90601933, 1.00865404, 4.18668554, 3.275571  ,
       1.33713321, 1.5085994 , 1.41301358, 3.41602734, 1.70679956,
       1.98557144, 1.64626028, 2.07196193, 3.62738717, 1.80882464,
       4.89214404, 5.46600355, 3.29862884, 4.91519677, 3.20638477,
       1.08286598, 1.01904357, 3.03314879, 1.27931264, 2.35336144,
       2.33767768, 4.26660843, 2.66422036, 1.22426565, 3.86766446,
       1.36076809, 2.48523016, 4.05419086, 3.7486199 , 2.94395273,
       3.76636917, 5.09184976, 4.36826238, 1.65597018, 2.59421701,
       1.98956716, 3.37637032, 1.90376113, 3.03613431, 3.59919675,
       2.986469  , 2.6306347 , 2.8711705 , 3.23494121, 1.80763

In [ ]:
pd.DataFrame(y_pred).to_csv("cb_submit.tsv", sep="\t", header=None)

In [ ]:
from catboost import CatBoostRegressor, Pool

# Шаг 1: Кросс-валидация для определения best_iter
data_pool = Pool(X, y)

params = {
    'iterations': 5000,
    'learning_rate': 0.1,
    'loss_function': 'RMSE',
    'eval_metric': 'RMSE',
    'od_type': 'Iter',
    'od_wait': 50,
    'use_best_model': True
}

cv_data = cv(
    params=params,
    pool=data_pool,
    fold_count=5,
    shuffle=True,
    partition_random_seed=42,
    plot=True,
    verbose=False
)

best_iter = cv_data['iterations'].max()
print(f'Best number of iterations: {best_iter}')

# Шаг 2: Обучение модели с использованием best_iter
model = CatBoostRegressor(**params)
model.fit(
    X, y,
    eval_set=(X_test, y_test),  # Предполагается, что у вас есть валидационный набор
    use_best_model=True,
    verbose=False
)

# Шаг 3: Сохранение модели
model.save_model('best_model_cv.cbm')

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Training on fold [0/5]

bestTest = 0.8932734714
bestIteration = 2178

Training on fold [1/5]

bestTest = 0.8968460356
bestIteration = 2182

Training on fold [2/5]

bestTest = 0.889611475
bestIteration = 2021

Training on fold [3/5]

bestTest = 0.8888967378
bestIteration = 2628

Training on fold [4/5]

bestTest = 0.8920812945
bestIteration = 2407

Best number of iterations: 2678


In [ ]:
from sklearn.model_selection import GridSearchCV
from catboost import CatBoostRegressor

param_grid = {
    'depth': [4, 6, 8],
    'learning_rate': [0.01, 0.05, 0.1],
    'l2_leaf_reg': [1, 3, 5],
    'iterations': [500, 1000]
}

cb = CatBoostRegressor(loss_function='RMSE', eval_metric='RMSE', verbose=0)

grid_search = GridSearchCV(cb, param_grid, cv=3, scoring='neg_mean_squared_error', n_jobs=-1)
grid_search.fit(X_train, y_train)

print('Best parameters:', grid_search.best_params_)
print('Best CV score:', -grid_search.best_score_)

In [ ]:
from sklearn.model_selection import RandomizedSearchCV
import scipy

param_dist = {
    'depth': scipy.stats.randint(4, 10),
    'learning_rate': scipy.stats.uniform(0.01, 0.1),
    'l2_leaf_reg': scipy.stats.randint(1, 10),
    'iterations': scipy.stats.randint(500, 2000)
}

random_search = RandomizedSearchCV(cb, param_distributions=param_dist, n_iter=50, cv=3, scoring='neg_mean_squared_error', n_jobs=-1, random_state=42)
random_search.fit(X_train, y_train)

print('Best parameters:', random_search.best_params_)
print('Best CV score:', -random_search.best_score_)

In [ ]:
import optuna
from catboost import CatBoostRegressor, Pool
import numpy as np

def objective(trial):
    params = {
        'iterations': 2000,
        'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.1),
        'depth': trial.suggest_int('depth', 4, 10),
        'l2_leaf_reg': trial.suggest_loguniform('l2_leaf_reg', 1e-3, 10),
        'bagging_temperature': trial.suggest_uniform('bagging_temperature', 0, 1),
        'random_strength': trial.suggest_uniform('random_strength', 0, 1),
        'loss_function': 'RMSE',
        'eval_metric': 'RMSE',
        'od_type': 'Iter',
        'od_wait': 50
    }

    # Инициализация CatBoostRegressor с гиперпараметрами
    model = CatBoostRegressor(**params, verbose=0)

    # Выполнение кросс-валидации
    cv_results = cv(
        params,
        Pool(X_train, y_train),
        fold_count=3,
        shuffle=True,
        partition_random_seed=42,
        verbose=False
    )

    # Извлечение наилучшего значения RMSE
    best_rmse = np.min(cv_results['test-RMSE-mean'])

    return best_rmse

# Создание исследования и оптимизация целевой функции
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=50)

print('Лучшие параметры:', study.best_params)
print('Лучшее значение RMSE:', study.best_value)